# crawler


In [1]:
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
import time
from selenium.webdriver.common.action_chains import ActionChains 
import json

<div dir="rtl">
در این بخش ابتدا کد های لازم برای تابع را به صورت جدا بررسی میکنیم و سپس همه ی آنها را در قالب یک تابع داریم.
    <br>
    در قسمت اول باید یک درایور تعریف کنیم. مااز درایور گوگل کروم استفاده کردیم و فایل مربوط به آن در قسمت data قرار دارد. برای user agent هم گوگل کروم را اضافه کردیم.
</div>

In [2]:
options = webdriver.ChromeOptions()
options.add_experimental_option("excludeSwitches", ["enable-automation"])
options.add_experimental_option('useAutomationExtension', False)
options.add_argument("--headless")
options.add_argument("user-agent=Chrome/88.0.4324.96 Safari/537.36")
driver = webdriver.Chrome(options=options, executable_path="./chromedriver")

<div dir="rtl">
در این بخش یک درخواست get میفرستیم تا محتوای url را دریافت کنیم.
</div>

In [3]:
url = "https://academic.microsoft.com/paper/2981549002"
driver.get(url)

<div dir="rtl">
در بخش قبل با فرستادن درخواست متوجه شدیم که وقتی درخواست فرستاده میشود کل محتوای صفحه یکجا لود نمیشود در نتیجه وقتی دنبال بعضی از عناصر میگشنیم چون هنوز لود نشده بودند پیدا نمیکرد.
<br>
کد زیر ابتدا تا آخر صفحهscroll میکند تا همه ی محتوا لود شود.
</div>

In [4]:
# Scroll page to load whole content
last_height = driver.execute_script("return document.body.scrollHeight")
while True:
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    time.sleep(2)
    new_height = driver.execute_script("return document.body.scrollHeight")
    if new_height == last_height:
        break
    last_height = new_height
# element_to_hover_over = driver.find_element_by_class_name("icon-reading_list") 
# ActionChains(driver).move_to_element(element_to_hover_over).perform()

<div dir="rtl">
در این بخش کد اطلاعات مورد نیاز را برای crawl کردن بدست می آوریم. برای پیدا کردن این اطلاعات از css selectorاستفاده میکنیم و برای پیدا کردن selectorهر عنصر هم از 
inspect element گوگل کروم استفاده کردیم.
</div>

In [602]:
id = [int(a) for a in url.split('/') if a.isdigit()==True][0]
print(id)
title = driver.find_elements_by_css_selector(".name")[0]
print(title.text)
abstract = driver.find_elements_by_css_selector(".name-section p")
print([a.text for a in abstract if a.text is not ''][0])
year = driver.find_elements_by_css_selector(".year , p")[0].text
print(year)
authers = driver.find_elements_by_css_selector(".name-section .authors")
print([au.text for au in authers])
el = driver.find_elements_by_css_selector("div.primary_paper")
for element in el:
    t = element.find_element_by_css_selector(".ma-card .paper .title")
    print(t.text, t.get_attribute("href"))

2981549002
Tensor Programs I: Wide Feedforward or Recurrent Neural Networks of Any Architecture are Gaussian Processes.
Wide neural networks with random weights and biases are Gaussian processes, as originally observed by Neal (1995) and more recently by Lee et al. (2018) and Matthews et al. (2018) for deep fully-connected networks, as well as by Novak et al. (2019) and Garriga-Alonso et al. (2019) for deep convolutional networks. We show that this Neural Network-Gaussian Process correspondence surprisingly extends to all modern feedforward or recurrent neural networks composed of multilayer perceptron, RNNs (e.g. LSTMs, GRUs), (nD or graph) convolution, pooling, skip connection, attention, batch normalization, and/or layer normalization. More generally, we introduce a language for expressing neural network computations, and our result encompasses all such expressible neural networks. This work serves as a tutorial on the *tensor programs* technique formulated in Yang (2019) and elucid

<div dir="rtl">
و در نهایت باید درایور را ببندیم
</div>

In [3]:
driver.quit()

<div dir="rtl">
در نهایت همه ی بخش های کد های بالا را کنار هم قرار میدهیم و تابع web crawler را مینویسیم که این تابع با گرفتن حداکثر تعداد صفحات و مجموعه url اولیه crawl میکند.
   در این تابع یک آرایه از تمامی آی دی های crawl شده نگه میداریم تا هیچ صفحه ای را دوبار crawlنکند و علاوه بر این برای اینکه فقط یک نسخه را اضافه کند عنصر primary-paperرا استخراج میکنیم.
</div>

In [32]:
def web_crawler_to_json(MAX_PAGE_NUM, urls, DELAY):
    all_ids = []
    options = webdriver.ChromeOptions()
    options.add_experimental_option("excludeSwitches", ["enable-automation"])
    options.add_experimental_option('useAutomationExtension', False)
    options.add_argument("--headless")
    options.add_argument("user-agent=Chrome/88.0.4324.96 Safari/537.36")
    driver = webdriver.Chrome(options=options, executable_path="./chromedriver")
    page_num = 0
    articles = []
    while page_num < MAX_PAGE_NUM:
        current_url = urls.pop(0)
        current_id = [int(a) for a in current_url.split('/') if a.isdigit()==True][0]
        print(page_num, current_url)
        if current_id not in all_ids:
            driver.get(current_url)
            time.sleep(DELAY)
            last_height = driver.execute_script("return document.body.scrollHeight")
            while True:
                # Scroll down to the bottom.
                driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
                time.sleep(2)
                new_height = driver.execute_script("return document.body.scrollHeight")
                if new_height == last_height:
                    break
                last_height = new_height
    #         element_to_hover_over = driver.find_element_by_class_name("icon-reading_list") 
    #         ActionChains(driver).move_to_element(element_to_hover_over).perform()
            #extract information
            if driver.find_elements_by_css_selector(".name") == []:
                print("Network Error")
                urls.insert(0, current_url)
                continue
            print("____________________________________")
            id = [int(a) for a in current_url.split('/') if a.isdigit()==True][0]
            print(id)
            all_ids.append(id)
            title = driver.find_elements_by_css_selector(".name")[0].text
            print(title)
            abstract = driver.find_elements_by_css_selector(".name-section p")
            abstract = [a.text for a in abstract if a.text is not '']
            if len(abstract) != 0:
                abstract = abstract[0]
            else:
                abstract = ''
            print(abstract)
            year = driver.find_elements_by_css_selector(".year , p")[0].text
            print(year)
            authers = driver.find_elements_by_css_selector(".name-section .authors")
            authers = [au.text for au in authers]
            print(authers)
            el = driver.find_elements_by_css_selector("div.primary_paper")
            ref_array = []
            for element in el:
                t = element.find_element_by_css_selector(".ma-card .paper .title")
                refid = [int(a) for a in t.get_attribute("href").split('/') if a.isdigit()==True][0]
                urls.append(t.get_attribute("href"))
                ref_array.append(refid)
                print(refid, t.text,"*****", t.get_attribute("href"))
            article_dict = {
                "id": id,
                "title": title,
                "abstract": abstract,
                "date": year,
                "authors": authers,
                "references": ref_array
            }
            articles.append(article_dict)
            page_num += 1
    driver.quit()
    jsonString = json.dumps(articles)
    jsonFile = open("articles.json", "w")
    jsonFile.write(jsonString)
    jsonFile.close()

<div dir="rtl">
و در آخر با آدرس های داده شده در صورت سوال crawl میکنیم و نتیجه را در فایل articles.json ذخیره میکنیم.
</div>

In [33]:
MAX_PAGE_NUM = 1000
DELAY = 3
urls = ["https://academic.microsoft.com/paper/2981549002" ,
        "https://academic.microsoft.com/paper/3105081694" ,
        "https://academic.microsoft.com/paper/2950893734"]
web_crawler_to_json(MAX_PAGE_NUM, urls, DELAY)

0 https://academic.microsoft.com/paper/2981549002
____________________________________
2981549002
Tensor Programs I: Wide Feedforward or Recurrent Neural Networks of Any Architecture are Gaussian Processes.
Wide neural networks with random weights and biases are Gaussian processes, as originally observed by Neal (1995) and more recently by Lee et al. (2018) and Matthews et al. (2018) for deep fully-connected networks, as well as by Novak et al. (2019) and Garriga-Alonso et al. (2019) for deep convolutional networks. We show that this Neural Network-Gaussian Process correspondence surprisingly extends to all modern feedforward or recurrent neural networks composed of multilayer perceptron, RNNs (e.g. LSTMs, GRUs), (nD or graph) convolution, pooling, skip connection, attention, batch normalization, and/or layer normalization. More generally, we introduce a language for expressing neural network computations, and our result encompasses all such expressible neural networks. This work serve

2962793481 Unpaired Image-to-Image Translation Using Cycle-Consistent Adversarial Networks ***** https://academic.microsoft.com/paper/2962793481/reference
2963684088 Unsupervised Representation Learning with Deep Convolutional Generative Adversarial Networks ***** https://academic.microsoft.com/paper/2963684088/reference
2963373786 Improved techniques for training GANs ***** https://academic.microsoft.com/paper/2963373786/reference
2963470893 Photo-Realistic Single Image Super-Resolution Using a Generative Adversarial Network ***** https://academic.microsoft.com/paper/2963470893/reference
3 https://academic.microsoft.com/paper/2194775991/reference
____________________________________
2194775991
Deep Residual Learning for Image Recognition
Deeper neural networks are more difficult to train. We present a residual learning framework to ease the training of networks that are substantially deeper than those used previously. We explicitly reformulate the layers as learning residual functions

____________________________________
2964308564
Neural Machine Translation by Jointly Learning to Align and Translate
Abstract: Neural machine translation is a recently proposed approach to machine translation. Unlike the traditional statistical machine translation, the neural machine translation aims at building a single neural network that can be jointly tuned to maximize the translation performance. The models proposed recently for neural machine translation often belong to a family of encoder-decoders and consists of an encoder that encodes a source sentence into a fixed-length vector from which a decoder generates a translation. In this paper, we conjecture that the use of a fixed-length vector is a bottleneck in improving the performance of this basic encoder-decoder architecture, and propose to extend this by allowing a model to automatically (soft-)search for parts of a source sentence that are relevant to predicting a target word, without having to form these parts as a hard s

2153579005 Distributed Representations of Words and Phrases and their Compositionality ***** https://academic.microsoft.com/paper/2153579005/reference
2064675550 Long short-term memory ***** https://academic.microsoft.com/paper/2064675550/reference
2294059674 Maxout Networks ***** https://academic.microsoft.com/paper/2294059674/reference
2147768505 Context-Dependent Pre-Trained Deep Neural Networks for Large-Vocabulary Speech Recognition ***** https://academic.microsoft.com/paper/2147768505/reference
2132339004 A neural probabilistic language model ***** https://academic.microsoft.com/paper/2132339004/reference
6908809 ADADELTA: An Adaptive Learning Rate Method ***** https://academic.microsoft.com/paper/6908809/reference
1753482797 Recurrent Continuous Translation Models ***** https://academic.microsoft.com/paper/1753482797/reference
2156387975 Deep Sparse Rectifier Neural Networks ***** https://academic.microsoft.com/paper/2156387975/reference
2963504252 Exact solutions to the nonline

3118608800 Learning Multiple Layers of Features from Tiny Images ***** https://academic.microsoft.com/paper/3118608800/reference
2310919327 Gradient-based learning applied to document recognition ***** https://academic.microsoft.com/paper/2310919327/reference
2072128103 Learning Deep Architectures for AI ***** https://academic.microsoft.com/paper/2072128103/reference
2117130368 A unified architecture for natural language processing: deep neural networks with multitask learning ***** https://academic.microsoft.com/paper/2117130368/reference
2025768430 Extracting and composing robust features with denoising autoencoders ***** https://academic.microsoft.com/paper/2025768430/reference
2110798204 Greedy Layer-Wise Training of Deep Networks ***** https://academic.microsoft.com/paper/2110798204/reference
1498436455 Learning representations by back-propagating errors ***** https://academic.microsoft.com/paper/1498436455/reference
1994197834 An empirical evaluation of deep architectures on prob

...

2116064496 Training products of experts by minimizing contrastive divergence ***** https://academic.microsoft.com/paper/2116064496/reference
2117130368 A unified architecture for natural language processing: deep neural networks with multitask learning ***** https://academic.microsoft.com/paper/2117130368/reference
2025768430 Extracting and composing robust features with denoising autoencoders ***** https://academic.microsoft.com/paper/2025768430/reference
2110798204 Greedy Layer-Wise Training of Deep Networks ***** https://academic.microsoft.com/paper/2110798204/reference
983 https://academic.microsoft.com/paper/2148461049/reference
____________________________________
2148461049
Flexible, high performance convolutional neural networks for image classification
We present a fast, fully parameterizable GPU implementation of Convolutional Neural Network variants. Our feature extractors are neither carefully designed nor pre-wired, but rather learned in a supervised way. Our deep hierarch

2149684865 Text Categorization with Suport Vector Machines: Learning with Many Relevant Features ***** https://academic.microsoft.com/paper/2149684865/reference
1676552347 An Affine Invariant Interest Point Detector ***** https://academic.microsoft.com/paper/1676552347/reference
2124351082 Training support vector machines: an application to face detection ***** https://academic.microsoft.com/paper/2124351082/reference
2155511848 A statistical method for 3D object detection applied to faces and cars ***** https://academic.microsoft.com/paper/2155511848/reference
1484228140 Representing and Recognizing the Visual Appearance of Materials using Three-dimensional Textons ***** https://academic.microsoft.com/paper/1484228140/reference
986 https://academic.microsoft.com/paper/2100495367/reference
986 https://academic.microsoft.com/paper/3029645440/reference
986 https://academic.microsoft.com/paper/2110798204/reference
986 https://academic.microsoft.com/paper/2138857742/reference
986 https://a

1970789124 Natural gradient works efficiently in learning ***** https://academic.microsoft.com/paper/1970789124/reference
2045512849 The Geometry of Algorithms with Orthogonality Constraints ***** https://academic.microsoft.com/paper/2045512849/reference
1568229137 Adaptive Algorithms and Stochastic Approximations ***** https://academic.microsoft.com/paper/1568229137/reference
2104760318 Complexity Issues in Natural Gradient Descent Method for Training Multilayer Perceptrons ***** https://academic.microsoft.com/paper/2104760318/reference
2020107577 Adaptive natural gradient learning algorithms for various stochastic models ***** https://academic.microsoft.com/paper/2020107577/reference
1995842804 On-line learning in soft committee machines ***** https://academic.microsoft.com/paper/1995842804/reference
2047962774 Natural gradient descent for on-line learning ***** https://academic.microsoft.com/paper/2047962774/reference
2011055444 A dynamical model for the analysis and acceleration of

2912934387 Bagging predictors ***** https://academic.microsoft.com/paper/2912934387/reference
2155653793 The use of the area under the ROC curve in the evaluation of machine learning algorithms ***** https://academic.microsoft.com/paper/2155653793/reference
2155074104 A survey of kernel and spectral methods for clustering ***** https://academic.microsoft.com/paper/2155074104/reference
2152523366 Lagrangian support vector machines ***** https://academic.microsoft.com/paper/2152523366/reference
2089210920 OPLS discriminant analysis: combining the strengths of PLS-DA and SIMCA classification† ***** https://academic.microsoft.com/paper/2089210920/reference
2103914106 Kernel PCA for novelty detection ***** https://academic.microsoft.com/paper/2103914106/reference
2022279610 Optimal design of fuzzy classification systems using PSO with dynamic parameter adaptation through fuzzy logic ***** https://academic.microsoft.com/paper/2022279610/reference
1973041621 Finding the Number of Clusters in 

105804906 The ISOLET spoken letter database ***** https://academic.microsoft.com/paper/105804906/reference
997 https://academic.microsoft.com/paper/1541145887/reference
____________________________________
1541145887
Using the ADAP Learning Algorithm to Forecast the Onset of Diabetes Mellitus
Abstract Neural networks or connectionist models for parallel processing are not new. However, a resurgence of interest in the past half decade has occurred. In part, this is related to a better understanding of what are now referred to as hidden nodes. These algorithms are considered to be of marked value in pattern recognition problems. Because of that, we tested the ability of an early neural network model, ADAP, to forecast the onset of diabetes mellitus in a high risk population of Pima Indians. The algorithm's performance was analyzed using standard measures for clinical tests: sensitivity, specificity, and a receiver operating characteristic curve. The crossover point for sensitivity and sp

<div dir="rtl">
    کد زیر برای چک کردن این است که به هیچ لینکی دوبار درخواست نزده باشیم و همانطور که میبینید همه ی لینک ها فقط یک بار تکرار شده اند.
</div>

In [34]:
#loading the data from a file
f = open('articles.json','r')
s = f.read()
articles = json.loads(s)

In [35]:
from itertools import groupby
#extracting the gold clusters
def key_func(k): 
    return k['id']

p = sorted(articles, key=key_func) 

tag_number = 0
for key, value in groupby(p, key_func): 
    print(key, tag_number, len(list(value))) 
    tag_number += 1

4919037 0 1
6908809 1 1
10021998 2 1
19621276 3 1
21006490 4 1
36903255 5 1
44815768 6 1
51975515 7 1
60686164 8 1
71795751 9 1
82689443 10 1
104184427 11 1
137514618 12 1
139959648 13 1
179875071 14 1
181417509 15 1
189596042 16 1
194249466 17 1
196214544 18 1
196761320 19 1
203276351 20 1
205159212 21 1
607505555 22 1
639708223 23 1
648143168 24 1
753012316 25 1
830076066 26 1
1026270304 27 1
1423339008 28 1
1479807131 29 1
1482451543 30 1
1484228140 31 1
1486649854 32 1
1487641199 33 1
1490324987 34 1
1496357020 35 1
1498436455 36 1
1508165687 37 1
1510526001 38 1
1510543252 39 1
1511924373 40 1
1514535095 41 1
1517947178 42 1
1527772862 43 1
1528789833 44 1
1529008516 45 1
1531106656 46 1
1531648066 47 1
1533861849 48 1
1535810436 49 1
1536680647 50 1
1541145887 51 1
1544827683 52 1
1547224907 53 1
1549285799 54 1
1553702074 55 1
1554663460 56 1
1554944419 57 1
1560724230 58 1
1563088657 59 1
1565746575 60 1
1566135517 61 1
1568288633 62 1
1568307856 63 1
1573503290 64 1
1574901103

2795155917 714 1
2796426482 715 1
2797583072 716 1
2798766386 717 1
2798813531 718 1
2800783955 719 1
2804078698 720 1
2804822363 721 1
2806070179 722 1
2807736175 723 1
2810075754 724 1
2885050925 725 1
2886335102 726 1
2889758689 727 1
2891555348 728 1
2893749619 729 1
2895674046 730 1
2899771611 731 1
2903899730 732 1
2905573712 733 1
2907492528 734 1
2909194930 735 1
2911489562 736 1
2911964244 737 1
2912116903 738 1
2912565176 739 1
2912934387 740 1
2913535645 741 1
2913932916 742 1
2914120296 743 1
2914484425 744 1
2914746235 745 1
2919115771 746 1
2923014074 747 1
2933374552 748 1
2942841021 749 1
2949416428 750 1
2950893734 751 1
2951665052 752 1
2952509347 753 1
2952638691 754 1
2954064014 755 1
2955025503 756 1
2955425717 757 1
2962711740 758 1
2962736243 759 1
2962739339 760 1
2962754210 761 1
2962784628 762 1
2962790689 763 1
2962793481 764 1
2962795068 765 1
2962809918 766 1
2962820688 767 1
2962835968 768 1
2962851801 769 1
2962883549 770 1
2962883796 771 1
2962897886 772

## PageRank

<div dir="rtl">
حال به PageRank می پردازیم:
</div>

In [3]:
import networkx as nx
import numpy as np
import json

<div dir="rtl">
در این قسمت به خواندن از فایل جیسون به دست آمده از بخش قبل می پردازیم:
</div>

In [26]:
f = open('articles.json','r')
s = f.read()
articles = json.loads(s)
articles

[{'id': 2981549002,
  'title': 'Tensor Programs I: Wide Feedforward or Recurrent Neural Networks of Any Architecture are Gaussian Processes.',
  'abstract': 'Wide neural networks with random weights and biases are Gaussian processes, as originally observed by Neal (1995) and more recently by Lee et al. (2018) and Matthews et al. (2018) for deep fully-connected networks, as well as by Novak et al. (2019) and Garriga-Alonso et al. (2019) for deep convolutional networks. We show that this Neural Network-Gaussian Process correspondence surprisingly extends to all modern feedforward or recurrent neural networks composed of multilayer perceptron, RNNs (e.g. LSTMs, GRUs), (nD or graph) convolution, pooling, skip connection, attention, batch normalization, and/or layer normalization. More generally, we introduce a language for expressing neural network computations, and our result encompasses all such expressible neural networks. This work serves as a tutorial on the *tensor programs* techniqu

<div dir="rtl">
    حال باید گرافی بسازیم تا از روی لینک های هر id بتوانیم pagerank را محاسبه کنیم: 
</div>

In [27]:
G=nx.DiGraph()

<div dir="rtl">
در این مرحله باید نود های گراف را که شامل id ها می باشند اضافه کنیم:
</div>

In [28]:
ids = []
for i in range(len(articles)):
    ids += [str(articles[i].get('id'))]
#     print(str(articles[i].get('id')))
    for j in range(len(articles[i].get('references'))):
        if str(articles[i].get('references')[j]) not in ids:
            ids += [str(articles[i].get('references')[j])]
print(ids)
# for i in range(len(ids)):
G.add_nodes_from(ids)

['2981549002', '2194775991', '2963403868', '1836465849', '2964308564', '1677182931', '2963446712', '2157331557', '2310919327', '2064675550', '1533861849', '3105081694', '3001118548', '2962835968', '3008827533', '2919115771', '2108598243', '3007497549', '3010604545', '3008985036', '2950893734', '2964121744', '2117539524', '2099471712', '2963073614', '2962793481', '2963684088', '2963373786', '2963470893', '2194775991', '2618530766', '2097117768', '639708223', '2102605133', '1903029394', '2155893237', '1536680647', '2963403868', '2963341956', '2965373594', '2970597249', '2963091558', '2923014074', '2996428491', '2911489562', '2964110616', '1836465849', '2095705004', '2146502635', '1665214252', '2168231600', '104184427', '2964308564', '2294059674', '2132339004', '6908809', '1753482797', '1810943226', '2964199361', '2153653739', '1815076433', '1677182931', '2963446712', '2183341477', '2157331557', '2153579005', '2147768505', '2156387975', '2963504252', '2310919327', '2147880316', '215616311

<div dir="rtl">
نود ها به شکل زیر می باشند:</div>

In [29]:
G.nodes()

NodeView(('2981549002', '2194775991', '2963403868', '1836465849', '2964308564', '1677182931', '2963446712', '2157331557', '2310919327', '2064675550', '1533861849', '3105081694', '3001118548', '2962835968', '3008827533', '2919115771', '2108598243', '3007497549', '3010604545', '3008985036', '2950893734', '2964121744', '2117539524', '2099471712', '2963073614', '2962793481', '2963684088', '2963373786', '2963470893', '2618530766', '2097117768', '639708223', '2102605133', '1903029394', '2155893237', '1536680647', '2963341956', '2965373594', '2970597249', '2963091558', '2923014074', '2996428491', '2911489562', '2964110616', '2095705004', '2146502635', '1665214252', '2168231600', '104184427', '2294059674', '2132339004', '6908809', '1753482797', '1810943226', '2964199361', '2153653739', '1815076433', '2183341477', '2153579005', '2147768505', '2156387975', '2963504252', '2147880316', '2156163116', '2963399829', '2964311892', '2157364932', '1510526001', '1944615693', '2158778629', '2107878631', '

<div dir="rtl">
حال باید یال ها را حساب کنیم. هر یال شامل یک id و یکی از اعضای reference ها می باشد:
</div>

In [30]:
edges = []
for i in range(len(articles)):
    for j in range(len(articles[i].get('references'))):
        edges += [(str(articles[i].get('id')),str(articles[i].get('references')[j]))]
print(edges)

[('2981549002', '2194775991'), ('2981549002', '2963403868'), ('2981549002', '1836465849'), ('2981549002', '2964308564'), ('2981549002', '1677182931'), ('2981549002', '2963446712'), ('2981549002', '2157331557'), ('2981549002', '2310919327'), ('2981549002', '2064675550'), ('2981549002', '1533861849'), ('3105081694', '2194775991'), ('3105081694', '3001118548'), ('3105081694', '2962835968'), ('3105081694', '3008827533'), ('3105081694', '2919115771'), ('3105081694', '2108598243'), ('3105081694', '2963446712'), ('3105081694', '3007497549'), ('3105081694', '3010604545'), ('3105081694', '3008985036'), ('2950893734', '2964121744'), ('2950893734', '2963403868'), ('2950893734', '2117539524'), ('2950893734', '2099471712'), ('2950893734', '2964308564'), ('2950893734', '2963073614'), ('2950893734', '2962793481'), ('2950893734', '2963684088'), ('2950893734', '2963373786'), ('2950893734', '2963470893'), ('2194775991', '2618530766'), ('2194775991', '2962835968'), ('2194775991', '2097117768'), ('2194775

<div dir="rtl">
حالا به گراف یال ها را اضافه میکنیم:
</div>

In [31]:
G.add_edges_from(edges)

<div dir="rtl">
یال های گراف به شکل زیر می باشند:
</div>

In [32]:
G.edges()

OutEdgeView([('2981549002', '2194775991'), ('2981549002', '2963403868'), ('2981549002', '1836465849'), ('2981549002', '2964308564'), ('2981549002', '1677182931'), ('2981549002', '2963446712'), ('2981549002', '2157331557'), ('2981549002', '2310919327'), ('2981549002', '2064675550'), ('2981549002', '1533861849'), ('2194775991', '2618530766'), ('2194775991', '2962835968'), ('2194775991', '2097117768'), ('2194775991', '639708223'), ('2194775991', '1836465849'), ('2194775991', '2102605133'), ('2194775991', '2117539524'), ('2194775991', '1903029394'), ('2194775991', '2155893237'), ('2194775991', '1536680647'), ('2963403868', '2963341956'), ('2963403868', '2965373594'), ('2963403868', '2970597249'), ('2963403868', '2963091558'), ('2963403868', '2923014074'), ('2963403868', '2996428491'), ('2963403868', '2911489562'), ('2963403868', '2964110616'), ('1836465849', '2097117768'), ('1836465849', '2117539524'), ('1836465849', '2095705004'), ('1836465849', '1677182931'), ('1836465849', '2146502635')

<div dir="rtl">
حال با ورودی گرفتن آلفا می توانیم pagerank را محاسبه کنیم:</div>

In [33]:
print("Please enter alpha: ")
alpha = float(input())
pr = nx.pagerank(G, alpha)

Please enter alpha: 
0.9


<div dir="rtl">
pagerank  به دست آمده به شکل زیر می باشد:
</div>

In [34]:
pr

{'2981549002': 0.00016602671799423283,
 '2194775991': 0.0017708392809119078,
 '2963403868': 0.0008056333646874885,
 '1836465849': 0.0011143560948047378,
 '2964308564': 0.0006649038739049378,
 '1677182931': 0.0006571870998835683,
 '2963446712': 0.00034264041439326353,
 '2157331557': 0.0005473604327653291,
 '2310919327': 0.0032667821191018046,
 '2064675550': 0.0014635667141873097,
 '1533861849': 0.0006491698769390939,
 '3105081694': 0.00016602671799423283,
 '3001118548': 0.0011842247625669477,
 '2962835968': 0.001781906025604023,
 '3008827533': 0.0004057791335246848,
 '2919115771': 0.00024682752202123703,
 '2108598243': 0.001941893490643452,
 '3007497549': 0.0002570381980567846,
 '3010604545': 0.0004733489851016342,
 '3008985036': 0.000180991817876063,
 '2950893734': 0.00016602671799423283,
 '2964121744': 0.0009641584628450239,
 '2117539524': 0.001357128441274512,
 '2099471712': 0.0004955544983914602,
 '2963073614': 0.0004205848183549544,
 '2962793481': 0.000449318119258216,
 '2963684088